<div style="background-color:#E6FF94; color:#006769;">
    <h1><center>Greening the Urban Landscape: Assessing Tree Equity in New York City for Sustainable and Equitable Urban Policy</center></h1>
</div>

Courtesy: The Nature Conservancy

<div style="background-color:#DBE7C9; color:#294B29;">
    <h1><center>Policy</center></h1>
</div>

This policy proposal prioritises planting trees and investing in green infrastructure in neighbourhoods that have been identified as having poor tree equity scores in an effort to reduce the disparity of tree canopy coverage in New York City. The policy focuses on places that are particularly vulnerable because of environmental issues including poor air quality and increased susceptibility to heat waves, as well as social inequities. The plan calls for allocating funds based on the Tree Equity Score, a measure that integrates socioeconomic data and current canopy coverage. This would guarantee that tree planting initiatives support the larger objectives of advancing environmental justice and improving urban livability. This approach seeks to ensure that all communities, especially those that have historically been underserved, can benefit from urban forestry's reduced urban heat, improved air quality, and enhanced aesthetic value. It also aims to increase overall canopy coverage to the city-wide target of 30%.

<div style="background-color:#DBE7C9; color:#294B29;">
    <h1><center>Primary Data</center></h1>
</div>

This study used following dataset for all the analysis.

**canopy_jurisdiction_landuse_borough.zip** - Providing land and canopy area summaries by approximated general ownership type, land use categories, and natural/developed breakdown.

**canopy_streettree_summaries.zip** - Information about canopy and street tree summary data at the scales of Neighbourhood Tabulation Area, Community District, City Council District, and Borough.

**equity_data.zip** - This is the primary file used for this study to understand relationship between tree canopy and socioeconomic factors at the Neighbourhood Tabulation Area scale.

**naturalareas_canopy_jurisdiction_borough.zip** - Summaries of natural area canopy data by approximated general ownership type and by borough.

Source: https://zenodo.org/records/5210261

<div style="background-color:#DBE7C9; color:#294B29;">
    <h1><center>Supporting Data Source and Description</center></h1>
</div>

**Boundry Data**: Data for Borough and NTA boundry collected from NYC Department of Planning.
https://www.nyc.gov/site/planning/data-maps/open-data/census-download-metadata.page

- NTA: 2010 Neighborhood Tabulation Areas (NTAs) are medium-sized statistical geographies and each NTA contains enough population to mitigate sampling error although the boundaries and names of the 2010 Neighbourhood Tabulation Areas (NTAs) roughly correspond with many of the neighbourhoods that New Yorkers are familiar with, NTAs are not meant to be an exhaustive list of all possible names and understandings of neighbourhoods throughout New York City, nor are they meant to be a definitive representation of any particular neighbourhood.

**Land Surface Temperature**: Landsat Collection 2 U.S. Landsat Analysis Ready Data (ARD) product bundle
https://earthexplorer.usgs.gov/

- Data was downloaded from the USGS Earth Explorer, specifically Band 10, which pertains to surface temperature from the Landsat Collection 2 U.S. Landsat Analysis Ready Data (ARD) product bundle. The area was then clipped to the borough boundaries, which is the study area for this project. For a better understanding, the Digital Number (DN) values were converted from Kelvin to degrees Celsius using the following formula:

- ("LC08_L2SP_174038_20230716_20230725_02_T1_ST_B10.TIF" * 0.00341802 + 149 ) - 273.15

- Since the values are on a 30-meter spatial resolution, while converting raster to vector the majority value within each NTA area was chosen to represent the overall temperature for that area.

- All this process done in QGIS.

**Air Quality**: This dataset contain information about PM2.5, Nitrogen Dioxide and building emissions, building density, industrial areas, and traffic density air pollution to get deeper understanding of neighbourhood air quality.https://a816-dohbesp.nyc.gov/IndicatorPublic/data-features/neighborhood-air-quality/

**Public Health - Asthma**: A prevalent condition called asthma causes the lungs to swell and makes breathing difficult. In the poorest areas of New York City, asthma is a major cause of hospital stays, ER visits, and lost school days. Asthma is more prevalent in low-income Black and Latino youngsters in New York City. Asthma can be aggravated by smoke, air pollution, dust mites, cockroaches, mould, pollen, and pet dander. https://a816-dohbesp.nyc.gov/IndicatorPublic/data-explorer/asthma/?id=2384#display=summary

**Hurricane Evacuation Zones**: The different risk levels of flooding due to storm surge are represented by the hurricane evacuation zones around New York City. New York City Emergency Management (NYCEM) established these zones, and the Department of City Planning (DCP) was tasked with maintaining them. The hurricane evacuation preparations for New York City are based on six zones, with zone number one being the most vulnerable and zone number six being the least. https://data.cityofnewyork.us/Public-Safety/Hurricane-Evacuation-Zones/uihr-hn7s

**Street Data**: For comparison study, street data for Hunts Point were downloaded from open street map and later it clipped to residential area. 

**Street Tree**: Street tree data from NYC Parks & Recreation and partner organisations' TreesCount! 2015 Street Tree Census, which was carried out by volunteers and staff. Data on trees is collected on species, diameter, and overall health. Due to the granularity of the dataset, only Hunts Point street data used in this study. https://data.cityofnewyork.us/Environment/2015-Street-Tree-Census-Tree-Data/pi5s-9p35

**Grass/Shrub Land**: Land use land cover data used to clip open space areas for identify new potential sites for trees. Original data is in raster format. Data converted into vector format and class 2 which belongs to grass/shrubs clipped for study area. https://data.cityofnewyork.us/Environment/Landcover-Raster-Data-2010-3ft-Resolution/9auy-76zt/about_data

**Tree canopy**: An 6-inch resolution tree canopy change dataset covering the years 2010–2017 was created using data from the 2017 Light Detection and Ranging (LiDAR) survey categorises all tree polygons as follows: (1) None at All, (2) Profit, and (3) Loss. Due to size of the data, this data is not used in this study however its class gain and no change used to clip grass/shrub land from land cover data to create a land surface where tree canopy is absent which later used for tree planning analysis. https://data.cityofnewyork.us/Environment/Tree-Canopy-Change-2010-2017-/by9k-vhck/about_data

<div style="background-color:#DBE7C9; color:#294B29;">
    <h1><center>Libraries</center></h1>
</div>

In [ ]:
import pandas as pd
import matplotlib.pyplot as plt
import contextily as ctx
import plotly.express as px
import plotly.graph_objects as go
import plotly.figure_factory as ff
from plotly.subplots import make_subplots
import geopandas as gpd
import json
import numpy as np
import math
import rasterio
from rasterio.plot import show
import statsmodels.api as sm
import libpysal
from esda.moran import Moran
from splot.esda import plot_moran
from splot.esda import moran_scatterplot
import mgwr
from mgwr.gwr import GWR, MGWR
from mgwr.sel_bw import Sel_BW
from libpysal.weights.contiguity import Queen

<div style="background-color:#DBE7C9; color:#294B29;">
    <h1><center>Data Wrangling</center></h1>
</div>

### Boundry Shapefiles

#### Borough

The borough boundaries for New York City clipped to the shoreline

In [ ]:
# Load the shapefile
boro_boundry = gpd.read_file("Boundry/nybb_24a/nybb.shp")

In [ ]:
boro_boundry.plot()

In [ ]:
boro_boundry.crs

In [ ]:
# Changing name to match with all other dataset
boro_boundry = boro_boundry.rename(columns={"BoroName":"boroname"})

In [ ]:
boro_boundry.head()

### Neighbourhood Tabulation Area

In [ ]:
# Load the shapefile
nta_boundry_10 = gpd.read_file("Boundry/nynta2010_24a/nynta2010.shp")

In [ ]:
nta_boundry_10.plot()

In [ ]:
nta_boundry_10.crs

In [ ]:
nta_boundry_10 = nta_boundry_10.rename(columns={"NTAName": "ntaname", "NTACode":"ntacode"})

In [ ]:
nta_boundry_10.head()

In [ ]:
nta_boundry_10.info()

### Land Surface Temperature

In [ ]:
# Path to TIFF file
tif_path = 'Land Surface Temperature/lst_c_nyc.tif'

# Open the TIFF file
with rasterio.open(tif_path) as src:
    # Read the first band
    band1 = src.read(1)

In [ ]:
plt.figure(figsize=(10, 6))
plt.imshow(band1, cmap='magma')  
plt.colorbar(label='Temperature in Celsius')
plt.title('Land Surface Temperature Map')
plt.xlabel('Longitude')
plt.ylabel('Latitude')
plt.show()

In [ ]:
heat = gpd.read_file("Land Surface Temperature/lst_nta_nyc.shp")

In [ ]:
# Changing the column name majority to temperature
heat = heat.rename(columns={"_majority":"temperature","NTAName":"ntaname" })

In [ ]:
heat.head()

In [ ]:
heat.describe()

### Air Quality

In [ ]:
air_quality = pd.read_csv("Air Quality/aqe-nta.csv")

In [ ]:
air_quality.head()

In [ ]:
# rename the column name
air_quality.rename(columns={'NTA_NAME': 'ntaname', 'NTACODE': 'ntacode'}, inplace=True)

Air quality at the two sample locations that we ultimately used in our analysis of neighbourhood comparisons. As you can see, the Upper West Side, a commercial area of Manhattan, has high traffic air quality, while Hunts Points, the location of the largest food distribution centre, has high industrial air quality. 

In [ ]:
air_quality[air_quality['ntaname'] == 'Hunts Point']

In [ ]:
air_quality[air_quality['ntaname'] == 'Upper West Side (Central)']

### Public Health - Asthma

In [ ]:
asthma = pd.read_csv("Health/NYC EH Data Portal - Asthma emergency department visits (adults), by NTA (full table).csv")

In [ ]:
asthma.head()

In [ ]:
# rename the column name
asthma.rename(columns={'Geography': 'ntaname', 'Average annual number': 'Average annual number Asthma'}, inplace=True)

#### Top 5 Neighbourhood with Average Annual Number of Asthma Cases

In [ ]:
# Sorting the data by 'Average annual number Asthma' in descending order and selecting the top 5
top5_asthma = asthma.sort_values(by='Average annual number Asthma', ascending=False).head(5)

# Plotting the results
plt.figure(figsize=(10, 6))
plt.bar(top5_asthma['ntaname'], top5_asthma['Average annual number Asthma'], color='skyblue')
plt.xlabel('Neighborhood')
plt.ylabel('Average Annual Number of Asthma Cases')
plt.title('Top 5 Neighborhoods with Highest Average Annual Number of Asthma Cases')
plt.xticks(rotation=45)
plt.show()

<div style="background-color:#DBE7C9; color:#294B29;">
    <h1><center>Data Exploration</center></h1>
</div>

## Tree canopy by jurisdiction

In [ ]:
canopy_jd_landuse = pd.read_csv("canopy_jurisdiction_landuse_borough/canopy_jurisdiction_landuse_borough.csv")

In [ ]:
canopy_jd_landuse.head()

In [ ]:
canopy_jd_landuse.info()

#### Tree Canopy by Borough

In [ ]:
borough_share = canopy_jd_landuse.groupby('boroname')[['canopy2017_acres']].sum().reset_index()

In [ ]:
# Create a pie chart
fig_borough = px.pie(borough_share, values='canopy2017_acres', names='boroname', title='Distribution of NYC’s Tree Canopy by Borough')
fig_borough.update_traces(textposition='inside', textinfo='percent+label')
fig_borough.show()

By borough, canopy distribution also differs.  With its huge land area and mature trees, Queens is home to nearly one-third of all of New York City's tree canopy.  Not unexpectedly, Manhattan, the most developed and smallest borough in New York City, has only 7% tree canopy.

#### Land use associated with the respective row

In [ ]:
landuse_summary = canopy_jd_landuse.groupby('landuse_description')[['acreage']].sum().reset_index()

In [ ]:
# Create a pie chart using Plotly
fig_landuse = px.pie(landuse_summary, values='acreage', names='landuse_description', title='Landuse Coverage by Jurisdiction in 2017')
fig_landuse.show()

This pie chart illustrates the wide range of land use types found in New York City, emphasising the predominance of residential areas (single and multifamily) and the sizeable area under NYC Parks management. Notably, NYC Parks is in charge of a significant portion of city land, highlighting its function in maintaining green areas in the city. This distribution is important because it shows possible locations for urban forestry projects, particularly in residential areas where there may not be enough trees.

#### Tree Canopy Coverage

In [ ]:
coverage_summary = canopy_jd_landuse.groupby('assumed_owner_type')[['canopy2017_acres']].sum().reset_index()

In [ ]:
# Create a pie chart using Plotly
fig = px.pie(coverage_summary, values='canopy2017_acres', names='assumed_owner_type', title='Tree Canopy Coverage by Jurisdiction in 2017')
fig.show()

The percentage of the tree canopy covered by various entities is shown in the pie chart. It demonstrates that a sizeable portion of the canopy is privately owned, with notable contributions from various state and federal lands as well as those under city management. Much of the urban forest remains unprotected, though, as individual landowners are free to manage trees on their properties as they see suitable. The State permits local governments to set restrictions on the removal or destruction of trees to preserve and safeguard them, even on private property.

## Canopy data for natural areas in New York City by approximated general ownership type

In [ ]:
naturalareas_canopy = pd.read_csv("naturalareas_canopy_jurisdiction_borough/naturalareas_canopy_jurisdiction_borough.csv")

In [ ]:
naturalareas_canopy.head()

In [ ]:
coverage_by_jd = naturalareas_canopy.groupby('assumed_owner_type')['canopy2017_acres'].sum().reset_index()

In [ ]:
# Create a pie chart for the 2017 canopy coverage
fig = px.pie(coverage_by_jd, values='canopy2017_acres', names='assumed_owner_type', title='Tree Canopy Coverage by Jurisdiction in Natural Areas (2017)')
fig.show()

Highlighting the distribution of tree canopy in natural areas, shows that most of it is under municipal administration, with minor portions being overseen by state and federal agencies. This suggests that the upkeep and growth of green spaces in these vital natural areas which are essential to ecological stability and biodiversity are directly influenced by city policies.

#### NYC Park and Forever Wild Areas

The area (in acres) covered by each category to understand the proportion of land owned and managed by NYC Parks and the extent to which it is designated as Forever Wild

In [ ]:
# Calculate the total acreage for NYC Parks
nyc_parks_total_acreage = naturalareas_canopy[naturalareas_canopy['nycparks_land'] == 'NYC Parks']['acreage'].sum()

# Calculate the total acreage for Forever Wild areas within NYC Parks
forever_wild_total_acreage = naturalareas_canopy[(naturalareas_canopy['nycparks_land'] == 'NYC Parks') & (naturalareas_canopy['nycparks_foreverwild'] == 'Forever Wild')]['acreage'].sum()

In [ ]:
# Create a DataFrame for plotting
acreage_data = pd.DataFrame({
    'Category': ['NYC Parks', 'Forever Wild'],
    'Acreage': [nyc_parks_total_acreage, forever_wild_total_acreage]
})

In [ ]:
# Pie chart for NYC Parks land by acreage
fig_nyc_parks_acreage = px.pie(acreage_data, values='Acreage', names='Category', title='Acreage Distribution of NYC Parks Land')
fig_nyc_parks_acreage.show()

The land in NYC Parks is split between general parkland and Forever Wild areas, which are devoted to maintaining the city's natural landscapes. While the Forever Wild areas are essential for conservation efforts, the greater proportion of general parkland offers additional chances for recreational and aesthetic enhancements through urban forestry.

In [ ]:
# Comapring acreage_data 
fig = px.bar(acreage_data, x='Category', y='Acreage', title='Comparison of Acreage for NYC Parks vs. Forever Wild')
fig.show()

## Street Tree Summary 

### Borough

In [ ]:
street_trees_boro = pd.read_csv("canopy_streettree_summaries/canopystreettree_supp_boro.csv")

In [ ]:
street_trees_boro.info()

In [ ]:
street_trees_boro

#### Most Common Tree Species

In [ ]:
# the most common tree species
fig = px.pie(street_trees_boro, values='treecount2015_alive', names='spc_mostcommon_living', title='Most Common Tree Species in NYC')
fig.show()

There are many varities of tree species present in nyc park making urban forest diverse and the most common street trees in nyc city is London Planetree. 

#### Distribution of NYC Tree

In [ ]:
# Summarize tree counts by borough
tree_counts_by_borough = street_trees_boro.groupby('boroname')['treecount2015_alive'].sum().reset_index()

# Create a pie chart
fig = px.pie(tree_counts_by_borough, values='treecount2015_alive', names='boroname', title='Distribution of NYC’s Street Trees by Borough')
fig.update_traces(textposition='inside', textinfo='percent+label')
fig.show()

NYC Parks has conducted three decadal counts of street trees (1995-1996, 2005-2006, and 2015-2016). The number of street trees each borough in 2015 is summarised on the pie chart, over one third Queens has the highest percentage (36.5%) and Manhattan has the lowest (10%). 

#### Change of Canopy Cover

In [ ]:
# Calculate net canopy change percent for each borough
net_canopy_change_by_borough = street_trees_boro.groupby('boroname')['netcanopychange_percent'].mean().reset_index()  # Using mean to aggregate data

# Create a bar chart
fig = px.bar(net_canopy_change_by_borough, x='boroname', y='netcanopychange_percent',
             title='Yearly Change of Canopy Cover by Borough',
             labels={'netcanopychange_percent': 'Net Canopy Change (%)', 'boroname': 'Borough'})
fig.update_traces(marker_color=px.colors.sequential.Inferno)  
fig.show()

Staten Island has the most canopy change (2.3%) in contrast, Queens had the lowest rate of increase in canopy cover change (0.9%).

### Neighbourhood Tabulation Area

In [ ]:
street_trees_nta = pd.read_csv("canopy_streettree_summaries/canopystreettree_supp_nta.csv")

In [ ]:
street_trees_nta.info()

In [ ]:
street_trees_nta.head()

In [ ]:
# Summarize tree counts by NTA
tree_counts_by_nta = street_trees_nta.groupby('ntaname')['treecount2015_alive'].sum().reset_index()

# Sort data for better visualization
tree_counts_by_nta = tree_counts_by_nta.sort_values(by='treecount2015_alive', ascending=False)

# Create a bar chart
fig = px.bar(tree_counts_by_nta, x='ntaname', y='treecount2015_alive', title='Number of Living Street Trees by NTA',
             labels={'ntaname': 'Neighborhood Tabulation Area', 'treecount2015_alive': 'Count of Living Street Trees'})
fig.update_layout(xaxis={'categoryorder':'total descending'})
fig.show()

Number of living street in Annadale is highest whereas airport has the lowest count and thus it suffers land surface heat higher than any other land cover.

In [ ]:
# 'med_dbh_living' contains the median DBH values for trees that are alive
fig = px.histogram(street_trees_nta, x='med_dbh_living',
                   title='Distribution of Tree Diameter at Breast Height (DBH)',
                   labels={'med_dbh_living': 'DBH (inches)'},
                   nbins=30,  
                   template='plotly_white')

fig.update_layout(xaxis_title='Diameter at Breast Height (inches)',
                  yaxis_title='Number of Trees',
                  bargap=0.2)  

fig.show()

We may examine several aspects of the health of the urban forest, such as tree size and canopy cover. Young trees that can develop to replace older ones as they begin to die off would be present in a healthy urban forest. The distribution diameter at breast height, as shown in this bar graph, can be used to calculate the volume, biomass, and carbon storage capacity of trees for sustainable urban environments.

## Tree Equity Data

In [ ]:
equity = pd.read_csv("equity_data/equity_data_supp_nta.csv")

In [ ]:
equity.head()

In [ ]:
equity.info()

In [ ]:
# Sorting by 'netcanopychange_percent' to get the top and bottom 5
top_df = equity.nlargest(5, 'netcanopychange_percent')
bottom_df = equity.nsmallest(5, 'netcanopychange_percent')

# Combining the results
result_df = pd.concat([top_df, bottom_df])

# Plotting using Plotly
fig = px.bar(result_df, 
             x='ntaname', 
             y='netcanopychange_percent', 
             title='Top and Bottom 5 Neighborhoods by % Net Canopy Change',
             labels={'ntaname': 'Neighborhood', 'netcanopychange_percent': '% Net Canopy Change'},
             color='netcanopychange_percent',
             color_continuous_scale=px.colors.diverging.RdYlGn[::1]
            )
fig.update_layout(xaxis_title='Neighborhood',
                  yaxis_title='% Net Canopy Change',
                  coloraxis_colorbar=dict(title='% Change'))
fig.show()

Morrisania-Melrose has highest net canopy cover changer around 4% whereas West Bringhton has lowest net canopy cover change around -2%. We can see that top neighbourhoods in net canopy cover change are from Manhatten which commercial part of nyc city dominated by white and high per capita income people.

<div style="background-color:#DBE7C9; color:#294B29;">
    <h1><center>Visualisation</center></h1>
</div>

In [ ]:
# Convert CRS to EPSG:4326 for visualisation
boro_boundry = boro_boundry.to_crs(epsg=4326)
nta_boundry_10 = nta_boundry_10.to_crs(epsg=4326)

### Creating Dataframe for Visualisation and Analysis

#### Borough

In [ ]:
gdf_boroughs = boro_boundry.merge(street_trees_boro, on='boroname')

In [ ]:
gdf_boroughs.head(2)

#### NTA

In [ ]:
gdf_nta = nta_boundry_10.merge(equity, on='ntaname')

In [ ]:
# Land surface temperature data merge to add 'temperature' values
gdf_nta = gdf_nta.merge(heat[['ntaname', 'temperature']], on='ntaname', how='left')

In [ ]:
# Publich health data on asthma
gdf_nta = gdf_nta.merge(asthma[['ntaname', 'Average annual number Asthma']], on='ntaname', how='left')

In [ ]:
gdf_nta.columns

In [ ]:
gdf_nta.head()

In [ ]:
# Convert geometry to JSON
geojson = json.loads(gdf_boroughs.geometry.to_json())
geojson_nta = json.loads(gdf_nta.geometry.to_json())

### Tree Canopy Distribution by Borough

In [ ]:
fig_tree = px.choropleth(gdf_boroughs,
                    geojson=gdf_boroughs.geometry,
                    locations=gdf_boroughs.index,
                    color='canopy2017percent',
                    color_continuous_scale="Greens",
                    labels={'canopy2017percent': '% Total Canopy Present in 2017'},
                    title='Tree canopy distribution by Borough',
                    hover_name='boroname')
fig_tree.update_geos(fitbounds="locations", visible=False)
fig_tree.show()

About 22% of the canopy is found in the Manhattan which is commercial district of NYC. At 31%, Staten Island has the highest canopy cover. Roughly 18% of the boroughs, Brooklyn and Queens, are covered in trees.

### Canopy Cover Change by Borough

In [ ]:
fig = px.choropleth(gdf_boroughs,
                    geojson=gdf_boroughs.geometry,
                    locations=gdf_boroughs.index,
                    color='netcanopychange_percent',
                    color_continuous_scale="YlGn",
                    labels={'netcanopychange_percent': '% Net Canopy Change'},
                    title='Net Change in Canopy Cover by Borough',
                    hover_name='boroname')
fig.update_geos(fitbounds="locations", visible=False)
fig.show()

Staten Island has highest canopy cover change which is 2.3% whereas Queen has lowest 0.9% change. 

### Canopy Cover Change by NTA

In [ ]:
# Example: Mapping canopy change
fig_nta = px.choropleth(gdf_nta,
                    geojson=gdf_nta.geometry,
                    locations=gdf_nta.index,
                    color='netcanopychange_percent',
                    color_continuous_scale="Rainbow",
                    labels={'netcanopychange_percent': '% Net Canopy Change'},
                    title='Net Change in Canopy Cover by NTA',
                    hover_name='ntaname')
fig_nta.update_geos(fitbounds="locations", visible=False)
fig_nta.show()

The difference between canopy increase and canopy loss is known as net canopy change. The canopy of a tree grows when new trees are planted, old trees mature, and tiny seedlings emerge from seeds. Over time, trees may also lose their canopy. Storms bring down trees, which also gradually deteriorate due to physical and environmental stresses. As we can see southern part of Queens and Brooklyn has negative canopy cover change mostly beacuse of this areas oftenly affected by flood, hurricane strom. 

Planting trees is another essential step towards long-term canopy growth. The goal of planting one million young trees along streets, in parkland, and on other property parcels between 2008 and 2015 was accomplished by the MillionTreesNYC programme, a collaboration between NYC Parks and the New York Restoration Project. In the result we can see a good growth of canopy in areas like north Brooklyn, south Bronx and north of Manhatten which shows around 3 to 4 % growth in canopy change. 

### Tree Canopy

In [ ]:
# Mapping canopy change
fig_tree_can = px.choropleth(gdf_nta,
                    geojson=gdf_nta.geometry,
                    locations=gdf_nta.index,
                    color='canopy_2017_pct',
                    color_continuous_scale="BuGn",
                    labels={'canopy_2017_pct': 'Percent of land area covered by canopy in 2017'},
                    title='Tree Canopy Cover by NTA',
                    hover_name='ntaname')
fig_tree_can.update_geos(fitbounds="locations", visible=False)
fig_tree_can.show()

The basis of our investigation is the map showing the coverage of tree canopy in each of New York City's Neighbourhood Tabulation Areas (NTAs). The different levels of canopy coverage are shown in this visualisation, along with its vital function in reducing urban challenges. Studies highlight the fact that tree canopies are essential for enhancing the quality of the urban environment and not just decorative elements. They provide a major contribution to lowering air pollution and the urban heat island effect.

The vital cooling effects of vegetation are demonstrated by the noticeable drops in air temperature that occur in NYC regions with at least 30% tree canopy coverage. In order to optimise environmental and socioeconomic advantages, we advocate policies that aim for a minimum of 30% canopy coverage throughout all NTAs. This threshold is crucial to achieving our objectives. Improved tree cover is associated with lower cooling energy consumption, better air quality, and overall increased urban resilience to the effects of climate change.

Through the examination of tree canopy coverage in connection to socio-economic variables within NTAs, this project demonstrates how targeted urban forestry efforts can mitigate inequalities and advance environmental justice. 

As we can see in the map most of the Staten Island neighbourhoods has coverd with over 30% tree canopy whereas neighbourhoods in Brooklyn and South Bronx are below 20% canopy cover. Upon closer inspection of our findings, several regions that initially seem densely vegetated really contain pockets that are not, and vice versa. For instance, we can observe similar dynamics at work in two distinct areas of the Bronx. With a high concentration of white, rich, and green citizens, Riverdale (which faces northwest) has a low heat-vulnerability rating (HVI of 1 out of 5). Kingsbridge (to the southeast) has a high heat-vulnerability rating (HVI of 2 out of 5), is sparsely vegetated, and has a higher percentage of persons of colour and generally lower income households.

### Land Surface Temperature

In [ ]:
# Mapping temperature change
fig_heat = px.choropleth(gdf_nta,
                    geojson=gdf_nta.geometry,
                    locations=gdf_nta.index,
                    color='temperature',
                    color_continuous_scale="Turbo",
                    labels={'temperature': 'temperature in Celcius'},
                    title='Temperature in NYC',
                    hover_name='ntaname')
fig_heat.update_geos(fitbounds="locations", visible=False)
fig_heat.show()

Due to the heat island effect, which is caused by urban features that absorb and reflect solar radiation, daytime temperatures in metropolitan regions are often greater than in natural settings. The study claims that as a result, daily temperatures in metropolitan areas may be 1–7 degrees higher than in natural environments. This problem mostly affects vulnerable communities, who are frequently found in locations with less trees.

As we can see in the map south east part of Queens suffers high temperature and this area is dominated by minority people who faces the health issues due to heat.

### Public Health - Asthma

In [ ]:
# Mapping Asthma
fig_asthma = px.choropleth(gdf_nta,
                    geojson=gdf_nta.geometry,
                    locations=gdf_nta.index,
                    color='Average annual number Asthma',
                    color_continuous_scale="PuRd",
                    labels={'Average annual number Asthma': 'Average Annual Number'},
                    title='Average Annual Number - Asthma',
                    hover_name='ntaname')
fig_asthma.update_geos(fitbounds="locations", visible=False)
fig_asthma.show()

Certain environmental factors, such as air pollution, could cause an asthma attack or exacerbate symptoms. Neighbourhood like East New York, Central Harlem has higher number of Asthma hospitalisation and this areas are low in tree canopy cover as well as the land surface temperture is higher than neighbouring local areas. This areas also rank high in Heat Vulnerability index. 

### Heat Vulnerability Index

In [ ]:
# Mapping HVI
fig_hvi = px.choropleth(gdf_nta,
                    geojson=gdf_nta.geometry,
                    locations=gdf_nta.index,
                    color='hvi_rank',
                    color_continuous_scale="Plasma",
                    labels={'hvi_rank': 'Health and Mental Hygiene'},
                    title='Heat Vulnerability Index',
                    hover_name='ntaname')
fig_hvi.update_geos(fitbounds="locations", visible=False)
fig_hvi.show()

The NYC Department of Health and Mental Hygiene determined the Heat Vulnerability Index, which ranges from 1 (lowest) to 5 (highest). The following variables are used to calculate this: Climate, air conditioner prevalence, green space, poverty, and racial. 

The analysis relies heavily on this map, which highlights the critical need for focused interventions in high-risk locations. Lower tree canopy coverage is frequently found in areas with higher HVIs, highlighting the importance of urban greenery in reducing heat exposure. This study shows that a greater percentage of trees in the canopy cools the air and significantly lowers the HVI, which has an immediate effect on public health.

The HVI ensures that green infrastructure and tree planting initiatives are given top priority in the communities that stand to gain the most from them. The strategy of this study focuses on these areas in an effort to lessen heat related diseases and deaths, especially among the most vulnerable communities, and strengthen our city's ability to withstand rising temperatures brought on by climate change.

In map we can see the HVI rank for Staten Island neighbourhood is low with none of its neighbourhood has HVI rank 5. The Bronx and Brooklyn has most number of neighbourhood where HVI rank is 5.

#### Who actually benefits from the unequal distribution of urban forests in New York City?

### Per Capita Income

In [ ]:
# Mapping Income
fig_pci = px.choropleth(gdf_nta,
                    geojson=gdf_nta.geometry,
                    locations=gdf_nta.index,
                    color='pci',
                    color_continuous_scale="BuPu",
                    labels={'pci': 'Median Per Capita Income'},
                    title='Per Capita Income',
                    hover_name='ntaname')
fig_pci.update_geos(fitbounds="locations", visible=False)
fig_pci.show()

The Per Capita Income map shows the economic environment in each neighbourhood of New York City and sheds light on the interactions between urban greenery and economic issues. Greater tree canopy coverage is usually seen in higher income areas, which benefits the environment and improves quality of life. On the other hand, lowered canopy coverage is common in lower-income areas, which can worsen the urban heat island effect and restrict access to green areas. This discrepancy emphasises the necessity of fair urban forestry policies that give greening in low income neighbourhoods first priority in order to advance environmental justice and enhance quality of life.

The general opinion was that higher-income areas had more trees, but when we looked at Manhattan, the area with the highest income is midtown, and there are hardly any trees there. This is a reflection of the priotization of land use and cover towards densely populated, high rise areas.

### Poverty

In [ ]:
# Mapping Poverty
fig_poverty = px.choropleth(gdf_nta,
                    geojson=gdf_nta.geometry,
                    locations=gdf_nta.index,
                    color='povrate',
                    color_continuous_scale="OrRd",
                    labels={'povrate': 'Poverty Rate'},
                    title='Poverty Rate',
                    hover_name='ntaname')
fig_poverty.update_geos(fitbounds="locations", visible=False)
fig_poverty.show()

The distribution of poverty in New York City is depicted on this map, which also demonstrates a pronounced negative link between the percentage of trees canopy and poverty rates. Lack of green space can exacerbate the dangers associated with environmental health and heat vulnerability in high-poverty neighbourhoods specially in South Bronx where we seen higher number hospitalization in Asthma . Redressing this disparity is essential to promoting public health and urban resilience, particularly in impoverished areas. With the application of these insights, this study seeks to promote targeted tree planting programmes that, by providing cooling, improving air quality, and creating recreational areas, can lessen the negative effects of poverty.

### Minority

In [ ]:
# Mapping People of Color
fig_ppl_clr = px.choropleth(gdf_nta,
                    geojson=gdf_nta.geometry,
                    locations=gdf_nta.index,
                    color='pocrate',
                    color_continuous_scale="Purples",
                    labels={'pocrate': 'Minority'},
                    title='People of Color',
                    hover_name='ntaname')
fig_ppl_clr.update_geos(fitbounds="locations", visible=False)
fig_ppl_clr.show()

Areas with large proportions of racial and ethnic minorities which are frequently underserved in terms of urban forestry and green infrastructure are highlighted on the Minority Population map. Lower tree canopy levels in these neighbourhoods frequently result in higher temperatures and worse air quality.

Greater exposure to nature is known to provide a number of health benefits, including better blood pressure, mental and physical health, sleep, and cognitive performance. Minority areas in the US have more artificially created surface area, such as cement and asphalt, and less tree canopy than majority white neighbourhoods.

The NYC North and South has the densely populated areas of minority neighbourhoods. Saying, "Let's plant a tree in the middle of a park," may seem simple, but it won't have the same distributed impact as planting a tree in a community of colour that is underserved by trees.

### English Proficiency

In [ ]:
# Mapping the languange proficiency
fig_lang = px.choropleth(gdf_nta,
                    geojson=gdf_nta.geometry,
                    locations=gdf_nta.index,
                    color='limitedenglishrate',
                    color_continuous_scale="PuBu",
                    labels={'limitedenglishrate': 'Lack of English proficiency'},
                    title='Percentage of persons (age 5+) who speak English less than well',
                    hover_name='ntaname')
fig_lang.update_geos(fitbounds="locations", visible=False)
fig_lang.show()

This map illustrates the geographical dispersion of communities with sizable populations that do not speak English well, highlighting important overlaps with regions with sparse tree cover. Participating in community planning procedures and obtaining information about urban greening programmes may be hindered by limited English skills. By identifying these places, we can modify our communication and engagement tactics to involve non native English speakers in the conversation about urban forestry. This will guarantee that programmes for tree planting and maintenance are affordable for all locals, increasing their potential to improve community well being and reduce urban heat island effects.

### Hurricane Evacuation Zones

Hurricane Evacuation Zones are determined by New York City Emergency Management and represent varying threat levels of coastal flooding resulting from storm surge. Zone 1 is most imapctful area whereas zone 7 is least imapctful area.

In [ ]:
hcz = gpd.read_file("Flood Map/Hurricane Evacuation Zones/geo_export_2690a75e-d0c2-4d48-9b93-eb251392ff4a.shp")

In [ ]:
# 'hcz' is GeoDataFrame and it includes a 'hurricane_' column for classification
fig, ax = plt.subplots(1, 1, figsize=(15, 15))
hcz.plot(column='hurricane_', ax=ax, legend=True,
         legend_kwds={'title': "Evacuation Zones"})

ax.set_xlim([-74.05, -73.75])
ax.set_ylim([40.5, 41])

# Hide axis for a cleaner look
ax.set_axis_off()

# Add a title 
ax.set_title('NYC Hurricane Evacuation Zones', fontdict={'fontsize': '15', 'fontweight' : '3'})

plt.show()

As we seen our tree canopy and net change canopy cover map south part of Queens has falls in zone 1 and 2 which is most vulnerable to flood and oftnley affected by storm. Tree canopies are an essential part of the urban infrastructure in these areas, and their distribution and presence go beyond simple aesthetic improvements. Trees absorb excess rainfall and reduce runoff, acting as natural barriers against strong winds and flooding to lessen the effects of storms. 

Policymakers and urban planners might discover underserved areas without sufficient green coverage by overlaying data on tree canopy coverage on these evacuation zones. These locations may also overlap with regions of high hurricane susceptibility. The city's resilience might be greatly increased by giving priority to tree planting and the development of green infrastructure in these areas. This would not only increase the city's ability to endure storm impacts but also improve the general urban climate. 

### Scatter Plot to show relationship between tree canopy and various factors

In [ ]:
# Creating subplots
fig = make_subplots(rows=2, cols=2,
                    subplot_titles=('Canopy vs. Poverty Rate',
                                    'Canopy vs. People of Color Rate',
                                    'Canopy vs. Heat Vulnerability Index',
                                    'Canopy vs. Temperature'))

# Scatter plot for Poverty Rate vs Canopy Coverage
fig.add_trace(
    go.Scatter(x=gdf_nta['povrate'], y=gdf_nta['canopy_2017_pct'], mode='markers', name='Poverty Rate'),
    row=1, col=1
)

# Scatter plot for People of Color Rate vs Canopy Coverage
fig.add_trace(
    go.Scatter(x=gdf_nta['pocrate'], y=gdf_nta['canopy_2017_pct'], mode='markers', name='People of Color Rate'),
    row=1, col=2
)

# Scatter plot for HVI Rank vs Canopy Coverage
fig.add_trace(
    go.Scatter(x=gdf_nta['hvi_rank'], y=gdf_nta['canopy_2017_pct'], mode='markers', name='HVI Rank'),
    row=2, col=1
)

# Scatter plot for Temperature vs Canopy Coverage
fig.add_trace(
    go.Scatter(x=gdf_nta['temperature'], y=gdf_nta['canopy_2017_pct'], mode='markers', name='Temperature'),
    row=2, col=2
)

# Update layout to adjust titles and axis labels
fig.update_layout(height=800, width=800, title_text="Relationships between Tree Canopy and Various Factors",
                  showlegend=False)

# Update xaxis properties
fig.update_xaxes(title_text="Poverty Rate (%)", row=1, col=1)
fig.update_xaxes(title_text="People of Color Rate (%)", row=1, col=2)
fig.update_xaxes(title_text="HVI Rank", row=2, col=1)
fig.update_xaxes(title_text="Temperature (°C)", row=2, col=2)

# Update yaxis properties
fig.update_yaxes(title_text="Canopy Coverage (%)", row=1, col=1)
fig.update_yaxes(title_text="Canopy Coverage (%)", row=1, col=2)
fig.update_yaxes(title_text="Canopy Coverage (%)", row=2, col=1)
fig.update_yaxes(title_text="Canopy Coverage (%)", row=2, col=2)

# Show plot
fig.show()

- Canopy vs. Poverty Rate: There is no clear pattern in this plot suggesting that lower income areas may have less canopy coverage.
- Canopy vs. Rate of People of Colour: Cluster at the end of x axis shows that less canopy coverage links to high minority.
- canopy versus Heat Vulnerability Index (HVI): This stratified perspective may indicate that places more susceptible to heat waves may not always benefit from greater canopy coverage, which is an important way to reduce urban heat islands.
- Canopy vs. Temperature: Here, the relationship is not uniform, indicating other urban factors also influence local temperature variations.

### With Trend Line

In [ ]:
# Scatter plot with trend line for Tree Canopy vs. Poverty Rate
fig = px.scatter(data_frame=gdf_nta, 
                 x='canopy_2017_pct', 
                 y='povrate', 
                 trendline='ols',
                 labels={'canopy_2017_pct': 'Canopy Coverage (%)', 'povrate': 'Poverty Rate (%)'},
                 title='Relationship between Tree Canopy and Poverty Rate')

fig.show()

It is evident that the downward trend line predicts a decrease in the poverty rate as canopy coverage rises.

In [ ]:
# Scatter plot with trend line for Tree Canopy vs. People of Color
fig = px.scatter(data_frame=gdf_nta, 
                 x='canopy_2017_pct', 
                 y='pocrate', 
                 trendline='ols',
                 labels={'canopy_2017_pct': 'Canopy Coverage (%)', 'pocrate': 'People of Color'},
                 title='Relationship between Tree Canopy and People of Color')

fig.show()

The downward trend line for minorities is a clear sign that we should concentrate our tree planting efforts in areas with a large concentration of people of colour.

### Correlation Matrix

In [ ]:
columns = [
    'canopy_2017_pct', 'pci', 'povrate', 'gte65rate', 'lte17rate',
    'pocrate', 'hvi_rank', 'temperature','limitedenglishrate','Average annual number Asthma'
]

# Create a new DataFrame with selected columns for correlation analysis
data_for_correlation = gdf_nta[columns]

# Compute the correlation matrix
correlation_matrix = data_for_correlation.corr()

fig = px.imshow(
    correlation_matrix,
    text_auto=True,
    labels=dict(color="Correlation"),
    x=correlation_matrix.columns,
    y=correlation_matrix.columns,
    title="Correlation Matrix: Tree Canopy vs. Other Variables",
    color_continuous_scale='Viridis'  
)

# Update the layout to make the figure larger
fig.update_layout(
    autosize=False,
    width=800,  
    height=800,  
    margin=dict(l=20, r=20, t=50, b=20) 
)

# adjust the font size 
fig.update_traces(textfont_size=6)

# Show the figure
fig.show()

In this correlation matrics we can see that the realtionship between tree canopy and factors like poverty, literature, people of color, HVI, english languange proficiency and Asthma is negative it means improving canopy cover may help urban environment.

<div style="background-color:#DBE7C9; color:#294B29;">
    <h1><center>Analysis</center></h1>
</div>

For this study purpose Geographically Weighted Regression (GWR) and Ordinary Least Squares (OLS) regression applied to examine the factors influencing the coverage of urban tree canopy in New York City. These statistical models aided in identifying the environmental and social factors that influence the distribution of trees in different neighbourhoods.

Tree canopy cover and socioeconomic variables like the poverty rate and Heat Vulnerability Index (HVI) can be used to identify whether they are randomly distributed, dispersed, or clustered throughout New York City using spatial autocorrelation (Moran's I). This will reveal whether there is a geographic clustering of these variables' high or low values.

## Multiple Linear Regression 

In [ ]:
# Define the independent variables and add a constant to the model
X = gdf_nta[['pci','povrate','pocrate','limitedenglishrate','hvi_rank','lte17rate','gte65rate']]
X = sm.add_constant(X)  

# Define the dependent variable
y = gdf_nta['canopy_2017_pct']

# Fit the regression model
model = sm.OLS(y, X).fit()

# Print the summary of the regression
print(model.summary())

With an R-squared value of 0.288, the OLS model showed a somewhat positive fit, indicating that the chosen variables may account for roughly 28.8% of the variation in tree canopy coverage. 

showed a significant inverse relationship with canopy coverage, suggesting that neighbourhoods with greater levels of language barriers may receive less attention when it comes to planting and caring for trees.

Very negative, emphasising that the risks associated with heat are increased in places that are more vulnerable due to a reduced canopy cover.

### Analyzing the spatial distribution of tree canopy coverage using Moran's I

In [ ]:
y = gdf_nta['canopy_2017_pct'].values
w = libpysal.weights.Queen.from_dataframe(gdf_nta)  # Define spatial weights based on a Queen contiguity matrix
w.transform = 'r'  # Row-standardize the weights

In [ ]:
moran = Moran(y, w)
print(f"Moran's I: {moran.I}, p-value: {moran.p_sim}")

In [ ]:
# Plotting Moran's Scatterplot using the simplified function
fig, ax = plt.subplots(figsize=(8, 8))
moran_scatterplot(moran, ax=ax)
ax.set_title('Moran\'s I Scatterplot for Tree Canopy Coverage')
plt.show()

X-axis (Attribute): Represents the values of tree canopy coverage at each location

Y-axis (Spatial Lag): Represents the average value of tree canopy coverage of neighboring locations for each area

**Upper Right (High-High)**: regions with comparable high coverage surround this region with high tree canopy coverage.

**Lower Right (Low-High)**: regions with high coverage are enclosed by low coverage parts of tree canopy. To improve canopy consistency, these would be suitable locations for focused tree planting.

**Upper Left (High-poor)**: regions with poor coverage surround a high tree canopy. These regions may be exceptional or outliers due to their greater canopy cover.

**Lower Left (Low-Low)**: Low tree canopy coverage is surrounded by areas with correspondingly low coverage. This shows patches with little canopy cover, which may draw attention to neglected or underserved areas.

Red line, or trend line, slope indicates the overall Moran's I statistic, which calculates the total amount of spatial autocorrelation. Positive spatial autocorrelation is suggested by a positive slope, like this one does. This indicates that, more often than would be predicted if the spatial distribution were random, places with high tree canopy tend to be close to other high canopy areas, and areas with low canopy tend to be close to other low canopy areas.

High canopy areas tend to group together, suggesting possible disparities in the distribution of urban green spaces. This trend emphasises the necessity of strategic planning to guarantee fair access to the tree canopy, especially in neighbourhoods that are sensitive to heat waves and have low socioeconomic status.

### Geographic Weighted Regression

In [ ]:
# 'gdf_nta' is already a GeoDataFrame with necessary columns
gdf_nta['coordinates'] = list(zip(gdf_nta.geometry.centroid.x, gdf_nta.geometry.centroid.y))
coords = list(gdf_nta['coordinates'])

In [ ]:
# Define the independent variables (X) and dependent variable (y)
X = gdf_nta[['pci','povrate', 'pocrate', 'hvi_rank', 'limitedenglishrate']]
y = gdf_nta['canopy_2017_pct'].values.reshape((-1,1))

In [ ]:
# Convert to numpy arrays for compatibility with mgwr library
X = (gpd.pd.DataFrame(X)).values
y = y.reshape((-1, 1))

In [ ]:
# Create spatial weights matrix
w = Queen.from_dataframe(gdf_nta)
w.transform = 'r'

In [ ]:
# Select bandwidth for each variable 
bw = Sel_BW(coords, y, X, fixed=False, kernel='bisquare').search()

In [ ]:
# Fit the GWR model
model = GWR(coords, y, X, bw=bw, kernel='bisquare')
results = model.fit()

In [ ]:
# Output the results
print(results.summary())

GWR showing that the model explains about 70% of the variance whereas Adjusted R2 0.62 reflects the complexity but still shows a good explanatory power. A substantial improvement from multiple regression model where R2 reflects 0.26.

Model also explain the negative realtionship between HVI and English language proficiencey which indicates that higher tree canopy will takes down heat varaiblity index and canopy might reach to the people who does not speak english.

#### Coefficient Plot

In [ ]:
# 'results' is the GWR model results and 'gdf_nta' is the GeoDataFrame
gdf_nta['coef_hvi'] = results.params[:, 3]  # Index depends on the order in X
gdf_nta['coef_limitedenglishrate'] = results.params[:, 4]

# Plotting the coefficients for 'HVI'
fig, ax = plt.subplots(1, 2, figsize=(15, 8))
gdf_nta.plot(column='coef_hvi', ax=ax[0], legend=True,
             legend_kwds={'label': "Coefficient for HVI",
                          'orientation': "horizontal"})
ax[0].set_title('Local GWR Coefficients for HVI')

# Plotting the coefficients for 'limitedenglishrate'
gdf_nta.plot(column='coef_limitedenglishrate', ax=ax[1], legend=True,
             legend_kwds={'label': "Coefficient for English Languange",
                          'orientation': "horizontal"})
ax[1].set_title('Local GWR Coefficients for People of Limited English skills')

plt.show()

**HVI**: Except for a few places like the east Bronx, where yellow patches suggest a positive relationship, areas coloured in dark blue and light green indicate a strong negative link that is evident across New York City and tells us tree canopy coverage is strongly inversely correlated with HVI.

**Limited English Language**: The data throughout New York City amply demonstrates the negative correlation between a person's inability to speak English and the tree canopy, as predicted by our study given the dispersion of tree canopy.

#### Residual Plot

In [ ]:
# Adding residuals to the GeoDataFrame
gdf_nta['residuals'] = results.resid_response

# Plot residuals
fig, ax = plt.subplots(figsize=(8, 8))
gdf_nta.plot(column='residuals', ax=ax, legend=True,
             legend_kwds={'label': "Residuals", 'orientation': "horizontal"})
ax.set_title('Map of Residuals')
plt.show()

Green areas indicate where the model has under-predicted the canopy cover where actual canopy coverage is higher than predicted. Purple areas show where the model has over-predicted the canopy cover where actual canopy coverage is lower than predicted. Yellow regions are close to accurate predictions by the model.

## Tree Equity Score: A Tool for Prioritizing Urban Tree Canopy Investments

The creation of the Tree Equity Score is a key component of the project that aims to rectify the unequal distribution of tree canopy in New York City. This advanced measure is intended to direct investments and policy choices, guaranteeing that the advantages of urban forestry are distributed fairly among all communities especially the underprivileged ones.

**Purpose and Utility**
In order to improve socioeconomic equity and environmental justice in urban design, the Tree Equity Score is an essential tool. Through the incorporation of socio-economic characteristics including income levels, racial demographics, age distribution, poverty, language competence, and heat vulnarbility with data on tree canopy coverage, the score offers a thorough evaluation of each neighborhood's tree canopy requirements in relation to its vulnerability. The following priority levels are directly mapped from the Tree Equity Scores: None (100), Low (90-99), Moderate (80-89), High (70-79) and Highest (0-69).

**Advantages**
- Targeted Investments: By highlighting particular regions with the lowest tree canopy and most vulnerability, the score helps allocate resources where they will have the greatest impact on the general public's health and standard of living.

- Policy Guidance: With the help of the Tree Equity Score, policymakers may easily prioritise tree planting and maintenance initiatives by using data to identify places that, when improved, can make a substantial contribution to the creation of resilient and equitable urban landscapes. This strategy is in line with larger goals of urban planning, which are to ensure that all citizens of the city, irrespective of their financial situation, can take advantage of equal access to green spaces. The city's goal to promoting inclusivity and sustainability in its urban landscape is supported by this strategic prioritisation, which also helps justice historical inequities in the distribution of trees.

- Improving Public Health: Communities who are currently disadvantaged can immediately benefit from increased tree canopy as it can reduce energy costs, enhance air quality, and decrease the effects of urban heat islands.

**Application in this project**
The study relied on the Tree Equity Score to identify neighbourhoods with insufficient tree coverage as well as those with exacerbated environmental challenges because of socioeconomic limitations. The project's suggestions for a policy that pledges to maintain a minimum of 30% tree canopy coverage in all neighbourhoods are supported by this score, which guarantees that everyone can benefit from urban trees and promotes a more sustainable and healthy urban environment.

In [ ]:
# Creating data frame for tree equity score
tes = gdf_nta[['ntacode_x', 'ntaname','BoroCode',
       'Shape_Leng', 'Shape_Area', 'geometry', 'ntacode_y', 'boroname',
       'canopy_2017_pct', 'pci', 'povrate','limitedenglishrate',
       'gte65rate', 'lte17rate','pocrate','hvi_rank']]

In [ ]:
tes.head()

In [ ]:
# combine child and old age data to make singular information about Age
tes['children_senior_pct'] = tes['lte17rate'] + tes['gte65rate']

In [ ]:
#  Ensure that factors where higher values should result in lower priority 
#(like canopy coverage and income) are indeed inverted before normalization.
tes['canopy_2017_pct_adj'] = 1 - (tes['canopy_2017_pct'] / 100)
tes['pci_adj'] = 1 - (tes['pci'] / 100)

In [ ]:
# following factors takes into consideration to generate tree equity score
factors = ['canopy_2017_pct_adj', 'pci_adj', 'povrate', 'limitedenglishrate', 'children_senior_pct', 'pocrate', 'hvi_rank']

In [ ]:
#  normalization is applied so that all factors are on a 0 to 1 scale
for col in factors:
    tes[col + '_norm'] = (tes[col] - tes[col].min()) / (tes[col].max() - tes[col].min())

In [ ]:
# weights according to the intended impact of each factor
weights = {
    'canopy_2017_pct_adj_norm': 1.0,
    'pci_adj_norm': 1.0,
    'povrate_norm': 1.5,  # Higher impact
    'limitedenglishrate': 1.2,
    'children_senior_pct_norm': 1.0,
    'pocrate_norm': 1.2,
    'hvi_rank_norm': 1.5,   # Higher impact
}

In [ ]:
tes['tree_equity_score'] = sum(tes[col] * weight for col, weight in weights.items())

In [ ]:
# scale the score between 0 to 100
tes['tree_equity_score_scaled'] = 100 - (100 * (tes['tree_equity_score'] - tes['tree_equity_score'].min()) / (tes['tree_equity_score'].max() - tes['tree_equity_score'].min())).astype(int)

In [ ]:
# create a function to give priority score
def classify_priority(score):
    if score <= 69:
        return 'Highest'
    elif score <= 79:
        return 'High'
    elif score <= 89:
        return 'Moderate'
    elif score <= 99:
        return 'Low'
    else:
        return 'None'

In [ ]:
# apply the function
tes['priority_class'] = tes['tree_equity_score_scaled'].apply(classify_priority)

### Tree Equity Score Map

In [ ]:
# Tree Equity Score Map

fig_tes = px.choropleth(tes,
                        geojson=tes.geometry,
                        locations=tes.index,
                        color='tree_equity_score_scaled',
                        color_continuous_scale="ice",
                        labels={'tree_equity_score_scaled': 'Priority Score'},
                        title='Tree Equity Score',
                        hover_name='ntaname',
                        hover_data={  
                                    'canopy_2017_pct': True,  
                                    'hvi_rank': True,
                                    'priority_class':True})

# Update map settings
fig_tes.update_geos(fitbounds="locations", visible=False)

# Show the figure
fig_tes.show()

The Tree Equity Score makes it easier to identify the places most impacted by socioeconomic and environmental factor. We can look at the map to see who scored the lowest and then look into more details about the location in links with all the factors and based on that we can determine which places require more trees.

Beyond only the score, Tree Equity Score offers an extensive range of other information. All nta areas are graded according to their Tree Equity Scores within each borough. When comparing nta within the same borough, we can idetify areas of higher priority within same borough.

With only 9% of the total land area covered by tree canopy, Hunts Point has one of the lowest in nyc city. With an HVI rating of 5, Hunts Point is highly developed and industrialised. The highest priority class with a score of 46. Its nearby area, Soundview Castle, has a tree equity score of 76, which is significantly higher, and an HVI rank of 4, which is lower than Hunts Point. By using the Tree Equitiy Score, we are able to determine the inequality of the tree cover within a certain area and how that diversity affects the neighborhood's community.

### Tree Equity Priority Map

In [ ]:
# Mapping Tree Equity Score Priority
fig_prior = px.choropleth(tes,
                    geojson=tes.geometry,
                    locations=tes.index,
                    color='priority_class',
                    color_continuous_scale="ice",
                    labels={'priority_class': 'Priority Class'},
                    title='Tree Equity Priority Map',
                    hover_name='ntaname')
fig_prior.update_geos(fitbounds="locations", visible=False)
fig_prior.show()

This map emphasises the critical need for greening interventions in areas with insufficient canopy coverage by showing locations with 'high' and 'highest' priority for tree planting. By directing funds and efforts where they are most needed, these priority classifications help policymakers ensure that the advantages of tree canopy are equally distributed.

### Poverty Rate and Priority

In [ ]:
# plotting the distribution of poverty rate across different tree equity priority classes
fig = px.box(data_frame=tes, 
             y='povrate', 
             color='priority_class',
             labels={'povrate': 'Poverty Rate (%)'},
             title='Distribution of Poverty Rate by Tree Equity Priority Classes')

fig.update_traces(quartilemethod="inclusive")  
fig.show()

Most of the nta areas where poverty rate over 20% have highest priority. 

### People of Color and Priority

In [ ]:
# plotting the distribution of poverty rate across different tree equity priority classes
fig = px.box(data_frame=tes, 
             y='pocrate', 
             color='priority_class',
             labels={'pocrate': 'People of Color'},
             title='Distribution of People of Color Rate by Tree Equity Priority Classes')

fig.update_traces(quartilemethod="inclusive")  
fig.show()

Minority over 50% has highest, high and moderate priorities.

### People of English Proficiency

In [ ]:
# plotting the distribution of poverty rate across different tree equity priority classes
fig = px.box(data_frame=tes, 
             y='limitedenglishrate', 
             color='priority_class',
             labels={'limitedenglishrate': 'Lack of English Proficiency'},
             title='Distribution of People of English Proficiency by Tree Equity Priority Classes')

fig.update_traces(quartilemethod="inclusive")  
fig.show()

It is clearly present that nta areas where people lack in english speaking falls in highest priorities.

<div style="background-color:#DBE7C9; color:#294B29;">
    <h1><center>Case Study</center></h1>
</div>

## Comparative Analysis of Neighborhoods

This study uses a comparative analysis between two different neighbourhoods, Hunts Point and Upper West Side, to clearly illustrate the effects of tree equity ratings on urban communities. These neighbourhoods were chosen because of the disparity in their tree equity scores: the Upper West Side scored highly, whereas Hunts Point scored poorly.

**Highlight Disparities**: The study shows how differences in tree canopy might affect urban living conditions by comparing a neighbourhood with low tree coverage to one with high tree coverage. The consequences of uneven green space distribution are easier to see when compared to this striking contrast.

**Recognise Socioeconomic Interactions**: By comparing these neighbourhoods, it is possible to delve deeper into the ways in which the presence of trees affects other socioeconomic parameters, like access to green spaces, income levels, and health outcomes. This aids in comprehending the multifaceted effects of urban forestry programmes.

**Policy Implications**: The comparative analysis emphasises the necessity of targated tree-planting and tree-maintenance plans that give priority to underprivileged regions. It offers specific instances of how increasing tree equity can result in notable advancements in public health and environmental quality, strengthening policy suggestions with empirical data.

In [ ]:
ntas_to_compare = ['Hunts Point', 'Upper West Side'] 
compare_gdf = tes[tes['ntaname'].isin(ntas_to_compare)]

In [ ]:
compare_gdf['children_senior_pct'] = compare_gdf['lte17rate'] + compare_gdf['gte65rate']

In [ ]:
compare_gdf

### Compare Tree Canopy Coverage

In [ ]:
fig = px.bar(compare_gdf, x='ntaname', y='canopy_2017_pct',
             title="Tree Canopy Coverage in 2017",
             labels={"canopy_2017_pct": "% of Land Covered by Canopy", "ntaname": "NTA"})
fig.show()

Tree canopy coverage in Upper west side is much higher at 33.79% in comparison with 9.63% in Hunts Point.

### People of Color

In [ ]:
fig = px.pie(compare_gdf, names='ntaname', values='pocrate',
             title="Percentage of People of Color by NTA",
             labels={"pocrate": "% People of Color"})
fig.show()

People of colour make up 75% of the population of Hunts Point which is very high as compare to Upper West Side.

### Comparison between a low-scoring neighborhood and a high-scoring neighborhood

In [ ]:
data_matrix = [
    ["Metric", "Neighborhood A (Hunts Point)", "Neighborhood B (Upper West Side)"],
    ["Tree Equity Score", "46", "92"],
    ["Tree Priority Score", "Highest", "Low"],
    ["Tree Canopy Cover", "9.6%", "33.7%"],
    ["People of Color", "98.3%", "32.7%"],
    ["People in Poverty", "39.6%", "10.2%"],
    ["Per Capita Income", "13.6K", "106K"],
    ["People Lack in English Speaking", "21%", "4%"],
    ["Heat Vulnerablity Index", "5", "1"],
    ["Land Surface Temeprature", "20", "17"],
    ["Air Quality (PM 2.5)", "6.5", "6.0"],
    
]

fig = ff.create_table(data_matrix)
fig.show()

Hunts Point challenges with a meagre 9.6% tree canopy cover, as shown by its Tree Equity Score of 46. In sharp contrast, the Upper West Side has a lush 33.7% canopy coverage and a strong score of 92.

The disparities in these neighbourhoods' demographics and socioeconomic conditions highlight how urgently focused urban greening initiatives are needed. Hunts Point experiences high temperatures and a Heat Vulnerability Index of 5, which exacerbates the urban heat island effect and the socioeconomic difficulties in a community where 98.3% of residents are people of colour and nearly 40% live in poverty. Due to the socioeconomic vulnerabilities of the neighbourhood, the air quality here poses an even greater threat to the community's health, with PM2.5 levels at 6.5, just slightly higher than those on the Upper West Side, which is a more affluent neighbourhood (6.0).

On the other hand, the Upper West Side benefits from both less severe land surface temperatures and a Heat Vulnerability Index of just 1, indicating a sharp differential in environmental stress. The Upper West Side also has a greater per capita income and a lower percentage of individuals living in poverty. These requirements are more than just numerical values; they also speak to a more complex story of environmental justice and the necessity of fair policy intervention.

Hunts Point stands out as a crucial region for intervention as New York City attempts to improve living conditions throughout all of its neighbourhoods and strengthen its urban forest. In addition to trees, the community needs a coordinated plan of action to remove the barrier of poverty, heat, and linguistic isolation that envelops the area. Policies may create healthier, more sustainable urban environments by giving Hunts Point and other neighbourhoods top priority for greening initiatives. This can help close the gap between the city's underprivileged areas and its green spaces.

### Spider Chart for Comparison

In [ ]:
categories = [
    'Tree Equity Score', 'Tree Priority Score', 'Tree Canopy Cover',
    'People of Color', 'People in Poverty', 'Per Capita Income',
    'People Lack in English Speaking', 'Heat Vulnerability Index',
    'Land Surface Temperature', 'Air Quality (PM 2.5)'
]

# Data converted to comparable scales
data_hunts_point = [46, 1, 9.6, 98.3, 39.6, 13.6, 21, 5, 20, 6.5]
data_upper_west_side = [92, 5, 33.7, 32.7, 10.2, 106, 4, 1, 17, 6.0]

fig = go.Figure()

fig.add_trace(go.Scatterpolar(
    r=data_hunts_point,
    theta=categories,
    fill='toself',
    name='Hunts Point'
))

fig.add_trace(go.Scatterpolar(
    r=data_upper_west_side,
    theta=categories,
    fill='toself',
    name='Upper West Side'
))

fig.update_layout(
    polar=dict(
        radialaxis=dict(
            visible=True,
            range=[0, 100]  # Example range, adjust based on your data scaling
        )),
    title="Comparison of Neighborhood A (Hunts Point) vs Neighborhood B (Upper West Side)"
)

fig.show()

### Analysis of Tree Canopy Expansion in Hunts Point

A thorough investigation was carried out to determine the possibility of raising tree canopy coverage to the aim of 30% in order to solve the disparity in tree equity in Hunts Point. The process included a number of crucial steps:

**Current Canopy Assessment**: Using exisiting data about canopy cover, the initial analysis quantified the current tree canopy cover.

**Tree Canopy Requirement Calculation**: To determine how much more canopy Hunts Point would need in order to reach 30% coverage, thi study calculate total required and additional canopy area in sqft. This required figuring out how big the neighbourhood is overall and how much more green space is required.

**Finding Potential Planting Sites**: Only residential streets are taken into consideration when choosing an appropriate spot for new trees, as policy suggests that street trees are more beneficial when planted in communities than in other locations. The canopy diameter is estimated using the current dbh values. Potential sites are found in residential streets after measuring the canopy radius and allocating a buffer to the street. Subsequently, the forecast for the quantity of new trees and canopy cover was computed.

**Land Use Analysis for New Planting**: To find more planting places, open land data from land use and land cover datasets were used. In order to maximise the area accessible for future growth, these areas were carefully examined to make sure they did not overlap with the current canopy.

**Quantitative Projections**: The last phase entailed figuring out how many trees could be planted and how much canopy coverage would rise. This quantitative prediction showed how effective planting may fulfil canopy requirements, giving Hunts Point's urban forestry efforts a concrete objective.

#### Overview Status

In [ ]:
# Canopy goal for each nta areas in nyc
canopy_goal_percent = 30 

In [ ]:
current_canopy_percent = gdf_nta[gdf_nta['ntaname'] == 'Hunts Point']['canopy_2017_pct'].values[0]

In [ ]:
print(f"Current canopy cover: {current_canopy_percent}")

In [ ]:
additional_canopy_needed = max(0, canopy_goal_percent - current_canopy_percent)
print(f"Additional canopy coverage needed: {(additional_canopy_needed).round(2)}%")

### Opening Geographical Area, Residential Streets and Street Trees

In [ ]:
# Load the shapefile for Hunts Point
hunts_point_area = gpd.read_file("Boundry/Hunts Point/hunts_point.shp")

In [ ]:
hunts_point_area.plot()

In [ ]:
hunts_point_area.crs

#### Total Geographical Area in Square Feet

In [ ]:
# Calculate the area in square feet
hunts_point_area['area_sqft'] = hunts_point_area['geometry'].area

# Sum the areas if there are multiple polygons
total_area_sqft = hunts_point_area['area_sqft'].sum()
print(f"Total area of Hunts Point in square feet: {total_area_sqft.round()}")

Total area of Hunts Point in square feet: 49693162

#### Residential Streets

Only Residential streets are considered.

In [ ]:
hunts_street = gpd.read_file("Boundry/Hunts Point/hunts_street.shp")

In [ ]:
hunts_street.plot()

In [ ]:
hunts_street.crs

#### Street Trees

In [ ]:
# Load the street tree locations
street_trees = gpd.read_file("Boundry/Hunts Point/street_trees.shp")

In [ ]:
street_trees.plot()

In [ ]:
street_trees.crs

In [ ]:
street_trees.columns

In [ ]:
street_trees.info()

In [ ]:
# converting value into numeric
street_trees['tree_dbh'] = pd.to_numeric(street_trees['tree_dbh'], errors='coerce')

### Estimating Canopy Cover by DBH

In [ ]:
# Define a simple function to estimate canopy spread based on DBH
def estimate_canopy_area(dbh):
    #A simple estimation where canopy diameter is assumed to be DBH * factor
    canopy_diameter = dbh * 2  # Assuming the canopy diameter is twice the DBH
    radius = canopy_diameter / 2
    area = np.pi * (radius ** 2)
    return area

In [ ]:
# Apply this function to each tree
street_trees['canopy_area_sqft'] = street_trees['tree_dbh'].apply(estimate_canopy_area)

In [ ]:
# Calculate average canopy area per tree
average_canopy_area = street_trees['canopy_area_sqft'].mean()

In [ ]:
average_canopy_area = average_canopy_area.round()

In [ ]:
average_canopy_area

### Visualisation of Street Trees Distribution in Hunts Point

In [ ]:
# Plotting the trees to visualize their distribution
fig, ax = plt.subplots(figsize=(10, 10))
hunts_point_area.plot(ax=ax, color='none', edgecolor='black')
street_trees.plot(ax=ax, marker='o', color='green', markersize=5)
hunts_street.plot(ax=ax, marker='-', color='orange', markersize=1)
plt.title('Current Tree Distribution in Hunts Point')
plt.show()

### Calculation for filling the gap for tree canopy area

In [ ]:
total_area_sqft = 49693162 
current_canopy_percent = 9.63 / 100
additional_canopy_needed_percent = 20.37 / 100
total_canopy_needed_percent = round(current_canopy_percent + additional_canopy_needed_percent, 2)

In [ ]:
total_canopy_needed_percent

In [ ]:
# Calculate the total required canopy area for 30% coverage
total_required_canopy_area_sqft = round(total_area_sqft * total_canopy_needed_percent, 2)

# Calculate the current canopy area
current_canopy_area_sqft = round(total_area_sqft * current_canopy_percent, 2)

In [ ]:
current_canopy_area_sqft

In [ ]:
total_required_canopy_area_sqft

In [ ]:
# Calculate the additional canopy area needed
additional_canopy_area_sqft = total_required_canopy_area_sqft - current_canopy_area_sqft

In [ ]:
additional_canopy_area_sqft

In [ ]:
# each new tree will have an average canopy of 213 square feet calculated by dbh information of tree
average_new_tree_canopy_sqft = average_canopy_area

In [ ]:
# Calculate the number of new trees needed
number_of_new_trees_needed = additional_canopy_area_sqft / average_new_tree_canopy_sqft

In [ ]:
# number of trees neede to cover tree canopy
number_of_new_trees_needed

### Suitable Planting Area on Residential Streets

In [ ]:
# Assuming an average canopy radius (say 15 feet)
average_canopy_radius = 15
street_trees['buffer'] = street_trees.geometry.buffer(average_canopy_radius)

In [ ]:
# Create a single combined canopy coverage layer from individual tree buffers
canopy_coverage = street_trees['buffer'].unary_union

In [ ]:
# Determine the uncovered area within Hunts Point
potential_planting_area = hunts_point_area.geometry.unary_union.difference(canopy_coverage)

In [ ]:
# Buffer the roads to simulate potential planting spots along streets
roads_buffer = hunts_street.geometry.buffer(20)  

In [ ]:
# Intersect road buffers with potential planting areas to find suitable planting spots
suitable_planting_spots = roads_buffer.intersection(potential_planting_area)

In [ ]:
# Convert suitable planting spots to a GeoDataFrame
suitable_planting_spots_gdf = gpd.GeoDataFrame(geometry=gpd.GeoSeries(suitable_planting_spots), crs="EPSG:2263")

In [ ]:
suitable_planting_spots_gdf.plot()

### Project Canopy Area Based on New Trees

In [ ]:
# Calculate the area (in square feet) of each suitable planting spot
suitable_planting_spots_gdf['area_sqft'] = suitable_planting_spots_gdf['geometry'].area

In [ ]:
# Determine if there is enough room for the required number of trees
total_available_planting_area_sqft = suitable_planting_spots_gdf['area_sqft'].sum()
print(f"Total available planting area: {total_available_planting_area_sqft} square feet")

In [ ]:
# Assuming each tree requires a certain square footage
area_per_tree_sqft = round(total_required_canopy_area_sqft / number_of_new_trees_needed, 2)

In [ ]:
area_per_tree_sqft

In [ ]:
# Calculate how many trees can be planted in each suitable planting spot
suitable_planting_spots_gdf['trees_possible'] = suitable_planting_spots_gdf['area_sqft'] / area_per_tree_sqft

In [ ]:
# Sum up the potential trees and compare with the required number of trees
total_possible_trees = suitable_planting_spots_gdf['trees_possible'].sum()
print(f"Total possible trees that can be planted: {total_possible_trees.round()}")

In [ ]:
number_of_new_trees = total_possible_trees
average_canopy_per_tree = average_canopy_area  # in square feet

# Calculate total projected canopy area from new trees
total_projected_canopy_area = round(number_of_new_trees * average_canopy_per_tree, 2)

In [ ]:
total_projected_canopy_area

### Suitable Tree Planting Location

In [ ]:
fig, ax = plt.subplots(figsize=(10, 10))
hunts_point_area.plot(ax=ax, color='none', edgecolor='black')
suitable_planting_spots_gdf.plot(ax=ax, color='green', alpha=0.5)
plt.title('Suitable Tree Planting Locations in Hunts Point')
plt.show()

### How much percentage canopy added

In [ ]:
total_projected_canopy_area = 4250347.53
total_area_sqft = 49693162.0
# Calculate the percentage of the total area this new canopy covers
projected_increase_percent = (total_projected_canopy_area / total_area_sqft) * 100

In [ ]:
projected_increase_percent

### Additional Tree Canopy in Open Land

Land cover data was obtained from NYC Open Data, focusing specifically on Class 2, which includes grass and shrub areas such as parks, open spaces, and backyards. To identify spaces available for new tree planting, this land cover data was overlaid with tree canopy data. Using QGIS, areas already covered by tree canopy were subtracted from the land cover data to ensure the remaining land is open and suitable for new tree plantations.

In [ ]:
open_land = gpd.read_file("Land Cover/hunts_open_land.shp")

In [ ]:
open_land.plot()

In [ ]:
open_land.crs

### Estimate Tree Canopy Coverage

In [ ]:
# Calculate the total area available in open land parcels
total_available_open_land_area = open_land['geometry'].area.sum()
print(f"Total Available Open Land Area: {total_available_open_land_area} square feet")

In [ ]:
average_canopy_per_tree = average_canopy_area

In [ ]:
average_canopy_per_tree

In [ ]:
# Calculate how many trees can be planted in open land parcels
number_of_trees_open_land = round(total_available_open_land_area / average_canopy_per_tree)
print(f"Number of Trees that can be Planted in Open Land Parcels: {number_of_trees_open_land}")

In [ ]:
# Calculate the projected canopy area these trees will cover
projected_canopy_area_open_land = round(number_of_trees_open_land * average_canopy_per_tree, 2)
print(f"Projected Canopy Area from Open Land Planting: {projected_canopy_area_open_land} square feet")

In [ ]:
# Calculate the new total projected canopy area including both streets and open land parcels
new_total_projected_canopy_area = total_projected_canopy_area + projected_canopy_area_open_land

In [ ]:
current_canopy_percent = 9.63  # Current canopy coverage in percent
new_total_canopy_coverage_percent = current_canopy_percent + projected_increase_percent

print(f"Updated Total Canopy Coverage Percentage: {new_total_canopy_coverage_percent:.2f}%")

Around 10% tree canopy can be added in Hunts Point. Later examination this study tested how hvi rank differ if canopy cover increased by 10%.

<div style="background-color:#DBE7C9; color:#294B29;">
    <h1><center>Policy Implication</center></h1>
</div>

In [ ]:
tcq = gdf_nta.copy()

In [ ]:
tcq.head()

### Determine the effect of a 10% increase in tree canopy on the Heat Vulnerability Index (HVI)

In [ ]:
# 'canopy_2017_pct' and 'hvi_rank' are columns in dataframe
print(tcq[['canopy_2017_pct', 'hvi_rank']].describe())

In [ ]:
# Example of a simple predictive model
# Let's say geographic weighted regression analysis found that for every 10% increase in tree canopy, HVI decreases by  -2.001 points

def predict_hvi_change(current_canopy, additional_canopy):
    # Assuming each 1% increase in canopy decreases HVI by 0.2001 points
    hvi_change = additional_canopy * -0.2001  
    return hvi_change

In [ ]:
# Applying a 10% increase in canopy to simulate changes
additional_canopy_percent = 10  
tcq['predicted_hvi_change'] = tcq['canopy_2017_pct'].apply(lambda x: predict_hvi_change(x, additional_canopy_percent))

In [ ]:
# Calculate the new HVI rank
tcq['new_hvi_rank'] = tcq['hvi_rank'] + tcq['predicted_hvi_change']
tcq['new_hvi_rank'] = tcq['new_hvi_rank'].clip(lower=1, upper=5)

In [ ]:
fig, ax = plt.subplots(1, 2, figsize=(12, 6))
tcq.plot(column='hvi_rank', ax=ax[0], legend=True, cmap='plasma')
ax[0].set_title('Original HVI Ranks')

tcq.plot(column='new_hvi_rank', ax=ax[1], legend=True, cmap='plasma')
ax[1].set_title('Predicted HVI Ranks After 10% Canopy Increase')
plt.show()

As the map illustrates, a 10% increase in tree canopy may result in a lower HVI rating. None of the nta has a hvi rank of four or higher in the predicted map. The nta regions that were previously ranked as high as five, including Hunts Point, now have a new rating of three after dropping two ranks, as seen by the predicted map.

This study suggest prioritise the location and targeted tree-planting programmes in high-priority locations determined by the Tree Equity Score findings. The benefits of greater canopy coverage would be fully realised with the strategic plantation of new trees, especially in populations that currently experience higher levels of heat vulnerability.